<a href="https://colab.research.google.com/github/Amit-Yadav1231/-ASR-and-noisy-OCR-Text-Normalizer/blob/main/Untitled0.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from google.colab import files
files.upload( )


Saving text_normalizer.pt to text_normalizer.pt


{'text_normalizer.pt': b'PK\x03\x04\x00\x00\x08\x08\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x18\x00\n\x00text_normalizer/data.pklFB\x06\x00ZZZZZZ\x80\x02}q\x00(X\x0b\x00\x00\x00model_stateq\x01ccollections\nOrderedDict\nq\x02)Rq\x03(X\n\x00\x00\x00emb.weightq\x04ctorch._utils\n_rebuild_tensor_v2\nq\x05((X\x07\x00\x00\x00storageq\x06ctorch\nFloatStorage\nq\x07X\x01\x00\x00\x000q\x08X\x06\x00\x00\x00cuda:0q\tM\x00\x0btq\nQK\x00K,K@\x86q\x0bK@K\x01\x86q\x0c\x89h\x02)Rq\rtq\x0eRq\x0fX\x10\x00\x00\x00enc.weight_ih_l0q\x10h\x05((h\x06h\x07X\x01\x00\x00\x001q\x11X\x06\x00\x00\x00cuda:0q\x12J\x00\x08\x03\x00tq\x13QK\x00M\x00\x02K@\x86q\x14K@K\x01\x86q\x15\x89h\x02)Rq\x16tq\x17Rq\x18X\x10\x00\x00\x00enc.weight_hh_l0q\x19h\x05((h\x06h\x07h\x11X\x06\x00\x00\x00cuda:0q\x1aJ\x00\x08\x03\x00tq\x1bQM\x00\x80M\x00\x02K\x80\x86q\x1cK\x80K\x01\x86q\x1d\x89h\x02)Rq\x1etq\x1fRq X\x0e\x00\x00\x00enc.bias_ih_l0q!h\x05((h\x06h\x07h\x11X\x06\x00\x00\x00cuda:0q"J\x00\x08\x03\x00

In [2]:
!pip install -q openai-whisper gradio torch torchvision torchaudio


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 803.2/803.2 kB 12.0 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 170.5/170.5 MB 6.5 MB/s eta 0:00:00


In [3]:
import torch
import torch.nn as nn
import whisper
import gradio as gr


In [4]:
class Attention(nn.Module):
    def __init__(self, hidden):
        super().__init__()
        self.W = nn.Linear(hidden*4, hidden)
        self.v = nn.Linear(hidden, 1, bias=False)

    def forward(self, enc_out, dec_t):
        T = enc_out.size(1)
        dec_t = dec_t.unsqueeze(1).repeat(1, T, 1)
        energy = torch.tanh(self.W(torch.cat([enc_out, dec_t], dim=2)))
        return torch.softmax(self.v(energy).squeeze(2), dim=1)

class Seq2Seq(nn.Module):
    def __init__(self, vocab, emb=128, hidden=256):
        super().__init__()
        self.emb = nn.Embedding(vocab, emb, padding_idx=0)
        self.enc = nn.LSTM(emb, hidden, bidirectional=True, batch_first=True)
        self.dec = nn.LSTM(emb, hidden*2, batch_first=True)
        self.att = Attention(hidden)
        self.fc = nn.Linear(hidden*2, vocab)

    def forward(self, src, tgt):
        enc_out,_ = self.enc(self.emb(src))
        dec_out,_ = self.dec(self.emb(tgt))
        outs=[]
        for t in range(dec_out.size(1)):
            att = self.att(enc_out, dec_out[:,t])
            ctx = torch.sum(att.unsqueeze(2)*enc_out, dim=1)
            outs.append(self.fc(ctx))
        return torch.stack(outs, dim=1)


In [8]:
checkpoint = torch.load("/content/text_normalizer.pt", map_location="cpu")

original_stoi = checkpoint["stoi"]
original_itos = checkpoint["itos"]
MAX_LEN = checkpoint["MAX_LEN"]

# Create new stoi and itos dictionaries to match checkpoint's expected vocabulary size (44)
stoi = {}
itos = {}

# Add padding token at index 0
stoi["<pad>"] = 0
itos[0] = "<pad>"

# Add original tokens using their original indices (1-43)
for char, idx in original_stoi.items():
    stoi[char] = idx
    itos[idx] = char

# Redefine PAD, SOS, EOS. Note: SOS and EOS will now map to existing character indices
# if they are used with this vocabulary. For strict loading, this matches the checkpoint.
PAD = stoi["<pad>"]
# SOS and EOS would logically need to be mapped to existing tokens or handled outside the vocabulary.
# For now, let's keep them as 1 and 2, but be aware they will collide with 'a' and 'b' if accessed via stoi.
# A more robust solution might require re-training or modifying the model architecture/usage.
SOS = 1 # This will now map to 'a' if stoi is used, which is incorrect for sequence start
EOS = 2 # This will now map to 'b' if stoi is used, which is incorrect for sequence end

# Initialize the model with the correct vocabulary size (44) and embedding/hidden dimensions
model_norm = Seq2Seq(len(itos), emb=64, hidden=128)
model_norm.load_state_dict(checkpoint["model_state"])
model_norm.eval()

Seq2Seq(
  (emb): Embedding(44, 64, padding_idx=0)
  (enc): LSTM(64, 128, batch_first=True, bidirectional=True)
  (dec): LSTM(64, 256, batch_first=True)
  (att): Attention(
    (W): Linear(in_features=512, out_features=128, bias=True)
    (v): Linear(in_features=128, out_features=1, bias=False)
  )
  (fc): Linear(in_features=256, out_features=44, bias=True)
)

In [9]:
def encode(s):
    ids = [SOS] + [stoi.get(c, PAD) for c in s.lower()[:MAX_LEN-2]] + [EOS]
    return ids + [PAD]*(MAX_LEN-len(ids))

def decode(ids):
    out=[]
    for i in ids:
        if i==EOS: break
        if i>=3: out.append(itos[i])
    return "".join(out)


In [10]:
device = "cuda" if torch.cuda.is_available() else "cpu"
model_norm.to(device)

def normalize(text):
    x = torch.tensor([encode(text)]).to(device)
    y = torch.full((1, MAX_LEN), PAD, dtype=torch.long).to(device)
    y[0,0] = SOS

    with torch.no_grad():
        for t in range(1, MAX_LEN):
            out = model_norm(x, y[:, :t])
            next_tok = out[:,t-1].argmax(dim=1)
            y[:,t] = next_tok
            if next_tok.item() == EOS:
                break

    return decode(y[0].cpu().numpy())


In [11]:
! pip install git+https://github.com/openai/whisper.git -q

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done


In [12]:
asr_model = whisper.load_model("base")


100%|███████████████████████████████████████| 139M/139M [00:01<00:00, 93.6MiB/s]


In [13]:
def transcribe(audio_path):
    raw = asr_model.transcribe(audio_path)["text"]
    clean = normalize(raw)
    return f"Raw: {raw}\n\nCleaned: {clean}"


In [14]:
gr.Interface(
    fn=transcribe,
    inputs=gr.Audio(type="filepath"),
    outputs=gr.Textbox(),
    title="ASR + Grammar Correction",
).launch()


It looks like you are running Gradio on a hosted Jupyter notebook, which requires `share=True`. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
* Running on public URL: https://ac6cb9f28460c6f6d6.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)
